# PLC 2024, Lecture 13, 22 February 2024

### Enumerated types

- Simplest form, choice of constants

In [2]:
enum IpAddrKind {
    V4,
    V6,
}

let four = IpAddrKind::V4;
let six = IpAddrKind::V6;


In [3]:
four

Error: `IpAddrKind` doesn't implement `Debug`

- Add special directive to get around the `Debug` issue

In [4]:
#[derive(Debug)]
enum IpAddrKind {
    V4,
    V6,
}

let four = IpAddrKind::V4;
let six = IpAddrKind::V6;


In [5]:
four

V4

- Options can be parameterized

In [6]:
#[derive(Debug)]
enum IpAddr {
    V4(String),
    V6(String),
}

let home = IpAddr::V4(String::from("127.0.0.1"));
let loopback = IpAddr::V6(String::from("::1"));


In [7]:
loopback

V6("::1")

- Another example

In [9]:
#[derive(Debug)]
enum IpAddr {
    V4(u8, u8, u8, u8),
    V6(String),
}

let home = IpAddr::V4(127, 0, 0, 1);
let loopback = IpAddr::V6(String::from("::1"));


In [10]:
home

V4(127, 0, 0, 1)

- Like a `struct`, can attach functions to an `enum`

In [11]:
#[derive(Debug)]
enum Message {
    Quit,
    Move { x: i32, y: i32 },
    Write(String),
    ChangeColor(i32, i32, i32),
}

impl Message {
    fn call(&self) {
        // method body would be defined here
    }
}

- Typical usage

In [12]:
let m = Message::Write(String::from("hello"));
m.call();

### Option type

- A type that can hold a value of type `T`, or be undefined

```
enum Option<T> {
    None,
    Some(T),
}
```
- Like `Maybe` in Haskell

- Examples (`Option` is a built-in enum)
- Note that `None` has to be explicitly typed

In [13]:
let some_number = Some(5);
let some_char = Some('e');

In [14]:
let absent_number: Option<i32> = None;

- Can't mix `T` and `Some(T)` in an expression

In [15]:
let x: i8 = 5;
let y: Option<i8> = Some(5);

let sum = x + y;


Error: consider importing one of these items

Error: cannot add `Option<i8>` to `i8`

- Need to `unwrap()` the inner value from `Some(T)`

In [16]:
let x: i8 = 5;
let y: Option<i8> = Some(5);

let sum = x + y.unwrap();


In [17]:
y

Some(5)

In [18]:
y.unwrap()

5

- Unwrapping `None` is an error

In [19]:
absent_number.unwrap()

thread '<unnamed>' panicked at src/lib.rs:158:15:
called `Option::unwrap()` on a `None` value
stack backtrace:
   0: rust_begin_unwind
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/std/src/panicking.rs:597:5
   1: core::panicking::panic_fmt
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/core/src/panicking.rs:72:14
   2: core::panicking::panic
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/core/src/panicking.rs:127:5
   3: <core::panic::unwind_safe::AssertUnwindSafe<F> as core::ops::function::FnOnce<()>>::call_once
   4: run_user_code_17
   5: evcxr::runtime::Runtime::run_loop
   6: evcxr::runtime::runtime_hook
   7: evcxr_jupyter::main
note: Some details are omitted, run with `RUST_BACKTRACE=full` for a verbose backtrace.


### Matching

- `match` operator selects amongst optional values in an `enum`

In [20]:
enum Coin {
    Penny,
    Nickel,
    Dime,
    Quarter,
}

fn value_in_cents(coin: Coin) -> u8 {
    match coin {
        Coin::Penny => {
            println!("Lucky penny!");
            1
        }
        Coin::Nickel => 5,
        Coin::Dime => 10,
        Coin::Quarter => 25,
    }
}



- `match` must return a consistent type

In [21]:
let z = match y {
    None => None,
    Some(x) => y.unwrap(),
};

Error: `match` arms have incompatible types

- This works

In [22]:
fn plus_one(x: Option<i32>) -> Option<i32> {
    match x {
        None => None,
        Some(i) => Some(i + 1),
    }
}

let five = Some(5);
let six = plus_one(five);
let none = plus_one(None);


In [23]:
five

Some(5)

In [24]:
six

Some(6)

In [25]:
none

None

- Can pattern match and operate within an enum
- **All** possible values must be covered -- error tells you which value was missed


In [26]:
fn plus_one(x: Option<i32>) -> Option<i32> {
    match x {
        Some(i) => Some(i + 1),
    }
}


Error: non-exhaustive patterns: `None` not covered

In [27]:
fn plus_one(x: Option<i32>) -> Option<i32> {
    match x {
        None => None,
        Some(i) => Some(i + 1),
    }
}

- `match` is not restricted to finite number of options
- `other` is a catch-all pattern

In [28]:
let dice_roll = 7;
match dice_roll {
    3 => add_fancy_hat(),
    7 => remove_fancy_hat(),
    other => move_player(other),
}

fn add_fancy_hat() {println!("Add fancy hat");}
fn remove_fancy_hat() {println!("Remove fancy hat");}
fn move_player(num_spaces: u8) {println!("Move {} spaces",num_spaces);}



Remove fancy hat


- If we don't need the value, can use anonymous `_` in place of `other`
  

In [29]:
let dice_roll = 9;
match dice_roll {
    3 => add_fancy_hat(),
    7 => remove_fancy_hat(),
    _ => reroll(),
}

fn add_fancy_hat() {println!("Add fancy hat");}
fn remove_fancy_hat() {println!("Remove fancy hat");}
fn reroll() {println!("Reroll");}


Reroll


### Panic

- Rust "panics" when it encounters an unrecoverable error at run-time

In [30]:
fn main() {
    let v = vec![1, 2, 3];

    v[99];
}


In [31]:
main()

thread '<unnamed>' panicked at src/lib.rs:50:6:
index out of bounds: the len is 3 but the index is 99
stack backtrace:
   0: rust_begin_unwind
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/std/src/panicking.rs:597:5
   1: core::panicking::panic_fmt
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/core/src/panicking.rs:72:14
   2: core::panicking::panic_bounds_check
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/core/src/panicking.rs:180:5
   3: <unknown>
   4: <unknown>
   5: evcxr::runtime::Runtime::run_loop
   6: evcxr::runtime::runtime_hook
   7: evcxr_jupyter::main
note: Some details are omitted, run with `RUST_BACKTRACE=full` for a verbose backtrace.


- We can invoke `panic()` with an error message

In [32]:
fn main() {
    panic!("Crash and burn!");
}


In [33]:
main()

thread '<unnamed>' panicked at src/lib.rs:48:5:
Crash and burn!
stack backtrace:
   0: rust_begin_unwind
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/std/src/panicking.rs:597:5
   1: core::panicking::panic_fmt
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/core/src/panicking.rs:72:14
   2: <unknown>
   3: <unknown>
   4: evcxr::runtime::Runtime::run_loop
   5: evcxr::runtime::runtime_hook
   6: evcxr_jupyter::main
note: Some details are omitted, run with `RUST_BACKTRACE=full` for a verbose backtrace.


### Result
- An enum to return informative error messages
```
enum Result<T, E> {
    Ok(T),
    Err(E),
}
```

- This code generates an error if `hello.txt` is not found in the current directory
- If the file can be opened, returns file handle for `hello.txt`

In [34]:
use std::fs::File;

fn main() {
    let greeting_file_result = File::open("hello.txt");

    let greeting_file = match greeting_file_result {
        Ok(file) => file,
        Err(error) => panic!("Problem opening the file: {:?}", error),
    };
}


In [35]:
main()

thread '<unnamed>' panicked at src/lib.rs:53:23:
Problem opening the file: Os { code: 2, kind: NotFound, message: "No such file or directory" }
stack backtrace:
   0: rust_begin_unwind
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/std/src/panicking.rs:597:5
   1: core::panicking::panic_fmt
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/core/src/panicking.rs:72:14
   2: <unknown>
   3: <unknown>
   4: <unknown>
   5: evcxr::runtime::Runtime::run_loop
   6: evcxr::runtime::runtime_hook
   7: evcxr_jupyter::main
note: Some details are omitted, run with `RUST_BACKTRACE=full` for a verbose backtrace.


- Here is what happens if `hello.txt` opens fine

In [36]:
use std::fs::File;

fn main() {
    let greeting_file_result = File::open("hello.txt");

    let greeting_file = match greeting_file_result {
        Ok(file) => {println!("Opened hello.txt"); file},
        Err(error) => panic!("Problem opening the file: {:?}", error),
    };
}



In [37]:
main()

Opened hello.txt


()

- Can `match` on type of error
- Can have nested (chained) errors

In [38]:
use std::fs::File;
use std::io::ErrorKind;

fn main() {
    let greeting_file_result = File::open("hello.txt");

    let greeting_file = match greeting_file_result {
        Ok(file) => file,
        Err(error) => match error.kind() {
            ErrorKind::NotFound => match File::create("hello.txt") {
                Ok(fc) => {println!("Created file!"); fc},
                Err(e) => panic!("Problem creating the file: {:?}", e),
            },
            other_error => {
                panic!("Problem opening the file: {:?}", other_error);
            }
        },
    };
}


In [39]:
main()

Created file!


()

- Shortcut: `unwrap()` extracts the match for the `OK` branch

In [40]:
use std::fs::File;

fn main() {
    let greeting_file = File::open("hello.txt").unwrap();
}


In [41]:
main()

()

- `expect()` is triggered by the `Err` branch and panics with a message

In [42]:
use std::fs::File;

fn main() {
    let greeting_file = File::open("hello.txt")
        .expect("hello.txt should be included in this project");
}



In [43]:
main()

thread '<unnamed>' panicked at src/lib.rs:51:10:
hello.txt should be included in this project: Os { code: 2, kind: NotFound, message: "No such file or directory" }
stack backtrace:
   0: rust_begin_unwind
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/std/src/panicking.rs:597:5
   1: core::panicking::panic_fmt
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/core/src/panicking.rs:72:14
   2: core::result::unwrap_failed
             at /rustc/a28077b28a02b92985b3a3faecf92813155f1ea1/library/core/src/result.rs:1652:5
   3: <unknown>
   4: <unknown>
   5: <unknown>
   6: evcxr::runtime::Runtime::run_loop
   7: evcxr::runtime::runtime_hook
   8: evcxr_jupyter::main
note: Some details are omitted, run with `RUST_BACKTRACE=full` for a verbose backtrace.


### Propagating errors
- The code below first tries to open `hello.txt`
- If this succeeds, it tries to read `username` from the file
- If either the file open or the file read fails, `Err(e)` is propagated to caller
  

In [44]:
use std::fs::File;
use std::io::{self, Read};

fn read_username_from_file() -> Result<String, io::Error> {
    let username_file_result = File::open("hello.txt");

    let mut username_file = match username_file_result {
        Ok(file) => file,
        Err(e) => return Err(e),
    };

    let mut username = String::new();

    match username_file.read_to_string(&mut username) {
        Ok(_) => Ok(username),
        Err(e) => Err(e),
    }
}
